In [2]:
import numpy as np
import open3d as o3d
from sklearn.cluster import KMeans
from sklearn.neighbors import NearestNeighbors
from scipy.sparse import csr_matrix, diags
from scipy.sparse.linalg import eigsh


## Method 1: Determining Curvature from Point Cloud Distribution using normals from neighboring points

In [26]:
pcd = o3d.io.read_point_cloud("./point_cloud_data/coupler/injection-molded-coupler.ply")
pcd = pcd.voxel_down_sample(voxel_size=0.005)
pcd.estimate_normals(search_param=o3d.geometry.KDTreeSearchParamHybrid(
    radius=0.02, max_nn=50))
X = np.asarray(pcd.points)

determine the curvature using the local surface variation

In [27]:

nn = 30
nbrs = NearestNeighbors(n_neighbors=nn, algorithm='kd_tree').fit(X)
idx = nbrs.kneighbors(return_distance=False)
curv = np.empty(len(X))
for i, N in enumerate(idx):
    P = X[N] - X[i]
    C = (P.T @ P) / (len(N)) 
    w = np.linalg.eigvalsh(C)        # λ1<=λ2<=λ3
    curv[i] = w[0] / (w.sum() + 1e-12)

In [28]:
k = 12
nbrs = NearestNeighbors(n_neighbors=k, algorithm='kd_tree').fit(X)
dist, inds = nbrs.kneighbors(X)
sigma2 = np.median(dist[:,1:]**2)  
rows, cols, vals = [], [], []
for i in range(len(X)):
    for d,j in zip(dist[i,1:], inds[i,1:]): 
        w = np.exp(-d*d / (sigma2+1e-12))
        rows += [i, j]; cols += [j, i]; vals += [w, w]
W = csr_matrix((vals,(rows,cols)), shape=(len(X),len(X)))
D = diags(np.ravel(W.sum(axis=1)))
L = D - W       # calculate the graph laplacian
# eigen-embeddings (lowest nontrivial eigenvectors)
m = 8
evals, evecs = eigsh(L.asfptype(), k=m+1, M=D.asfptype(), sigma=0.0)
spec = evecs[:,1:m+1]

group the features to run kmeans on them

In [29]:
N = np.asarray(pcd.normals)
feat = np.c_[curv, N, spec] # group the features
feat = (feat - feat.mean(0)) / (feat.std(0)+1e-12)

k_segments = 3
labels = KMeans(n_clusters=k_segments, n_init=10, random_state=0).fit_predict(feat)

3d visualizer

In [30]:
colors = np.random.RandomState(42).rand(k_segments,3)
pcd.colors = o3d.utility.Vector3dVector(colors[labels])
o3d.visualization.draw_geometries([pcd])

## Using Mesh

In [1]:
import numpy as np
import open3d as o3d
import igl
from sklearn.cluster import KMeans

# --- Load points & reconstruct a mesh (Poisson) ---
pcd = o3d.io.read_point_cloud("./point_cloud_data/shoe/shoe-dense.ply")
pcd = pcd.voxel_down_sample(0.003)
pcd.estimate_normals(o3d.geometry.KDTreeSearchParamHybrid(radius=0.01, max_nn=50))

mesh, _ = o3d.geometry.TriangleMesh.create_from_point_cloud_poisson(
    pcd, depth=10)                       # tune depth for fidelity vs smoothness
mesh = mesh.remove_unreferenced_vertices()
mesh = mesh.filter_smooth_taubin(number_of_iterations=10)
V = np.asarray(mesh.vertices); F = np.asarray(mesh.triangles)

# --- Principal curvatures (DDG) ---
k1, k2, d1, d2 = igl.principal_curvature(V, F)   # principal curvatures & dirs
H = 0.5*(k1 + k2)
K = k1 * k2

# --- Laplace–Beltrami spectra & HKS ---
L = igl.cotmatrix(V, F)                 # sparse
A = igl.massmatrix(V, F, igl.MASSMATRIX_TYPE_VORONOI)
# generalized eigs: L φ = λ A φ  (smallest λ)
evals, evecs = igl.eigs(L, A, 50)       # 50 eigenpairs (complex -> take real)
evals = np.real(evals); evecs = np.real(evecs)

def hks(evals, evecs, ts=(1e-4,1e-3,1e-2,1e-1)):
    # classic HKS: sum_k exp(-λ_k t) φ_k^2
    phi2 = evecs**2
    return np.stack([ (np.exp(-evals*t) @ phi2.T) for t in ts ], axis=1)

HKS = hks(evals, evecs)                 # (n_vertices, len(ts))

# --- Cluster on DDG features ---
feat = np.c_[H, K, HKS]
feat = (feat - feat.mean(0)) / (feat.std(0)+1e-12)
labels = KMeans(n_clusters=6, n_init=10, random_state=0).fit_predict(feat)

# --- Colorize & view ---
colors = np.random.RandomState(0).rand(labels.max()+1,3)
mesh.vertex_colors = o3d.utility.Vector3dVector(colors[labels])
o3d.visualization.draw_geometries([mesh])

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


ValueError: too many values to unpack (expected 4)

In [31]:
# DDG mesh segmentation (robust pyigl curvature unpack)
# ----------------------------------------------------
# pip install open3d pyigl numpy scipy scikit-learn

import numpy as np
import open3d as o3d
import igl
from sklearn.cluster import KMeans
from scipy.sparse.linalg import eigsh
from scipy.sparse import issparse

# ---------------------------
# Helpers
# ---------------------------

def robust_principal_curvature(V, F):
    """
    Call igl.principal_curvature with robust unpacking across pyigl builds.
    Returns:
        k1, k2 : (n,) float arrays   principal curvature values
        d1, d2 : (n,3) float arrays  principal directions
    """
    outs = igl.principal_curvature(V, F)

    # Typical wheels: (PD1, PD2, PV1, PV2)
    if isinstance(outs, tuple):
        if len(outs) >= 4:
            PD1, PD2, PV1, PV2 = outs[:4]
        else:
            raise RuntimeError(
                f"Unexpected number of outputs from principal_curvature: {len(outs)}"
            )
    else:
        # Very old style object with attributes
        PD1, PD2, PV1, PV2 = outs.PD1, outs.PD2, outs.PV1, outs.PV2

    # Ensure ndarray shapes
    PD1, PD2 = np.asarray(PD1), np.asarray(PD2)
    k1 = np.asarray(PV1).reshape(-1)
    k2 = np.asarray(PV2).reshape(-1)
    return k1, k2, PD1, PD2


def laplace_beltrami_spectrum(V, F, k=50):
    """
    Cotangent Laplacian (L) and Voronoi mass (A); generalized eig: L u = λ A u
    Returns (evals, evecs) with k smallest eigenpairs (excluding potential nullity issues).
    """
    L = igl.cotmatrix(V, F)                           # scipy.sparse CSR
    A = igl.massmatrix(V, F, igl.MASSMATRIX_TYPE_VORONOI)

    # Safety: ensure SciPy sparse (pyigl already returns CSR)
    assert issparse(L) and issparse(A), "Expected scipy.sparse matrices from libigl"

    # Shift-invert near 0.0 to get the smoothest modes first
    evals, evecs = eigsh(L.asfptype(), k=k, M=A.asfptype(), sigma=0.0)
    evals, evecs = np.real(evals), np.real(evecs)
    # Sort by eigenvalue just in case
    order = np.argsort(evals)
    return evals[order], evecs[:, order]


def hks_from_spectrum(evals, evecs, ts=(1e-4, 1e-3, 1e-2, 1e-1)):
    """
    Heat Kernel Signature at multiple time scales.
    HKS_t(i) = sum_k exp(-λ_k t) φ_k(i)^2
    """
    phi2 = evecs ** 2                     # (n, k)
    HKS = []
    for t in ts:
        coeff = np.exp(-evals * t)        # (k,)
        HKS.append(phi2 @ coeff)          # (n,)
    return np.stack(HKS, axis=1)          # (n, len(ts))


def poisson_mesh_from_pcd(pcd, depth=10, smooth_iters=10, crop_by_density=True):
    """
    Poisson reconstruct then optional Taubin smooth and (optionally) crop low density.
    Returns an Open3D TriangleMesh.
    """
    mesh, densities = o3d.geometry.TriangleMesh.create_from_point_cloud_poisson(
        pcd, depth=depth
    )
    mesh.remove_unreferenced_vertices()

    if crop_by_density:
        # Remove low-density vertices (heuristic cleanup)
        densities = np.asarray(densities)
        vmask = densities > np.quantile(densities, 0.05)
        mesh = mesh.select_by_index(np.where(vmask)[0])

    if smooth_iters and smooth_iters > 0:
        mesh = mesh.filter_smooth_taubin(number_of_iterations=smooth_iters)

    mesh.compute_vertex_normals()
    return mesh


# ---------------------------
# Main pipeline
# ---------------------------

def segment_mesh_ddg(
    point_cloud_path,
    voxel_size=0.003,
    normal_radius=0.01,
    normal_max_nn=50,
    poisson_depth=10,
    smooth_iters=10,
    n_eigs=50,
    k_clusters=6,
    hks_times=(1e-4, 1e-3, 1e-2, 1e-1),
):
    """
    End-to-end: point cloud -> Poisson mesh -> DDG features (curvatures + HKS) -> KMeans segmentation.
    Returns (mesh, labels) where labels are per-vertex cluster ids.
    """

    # 1) Load & preprocess point cloud
    pcd = o3d.io.read_point_cloud(point_cloud_path)
    if voxel_size and voxel_size > 0:
        pcd = pcd.voxel_down_sample(voxel_size)
    pcd.estimate_normals(
        o3d.geometry.KDTreeSearchParamHybrid(radius=normal_radius, max_nn=normal_max_nn)
    )

    # 2) Poisson mesh (robust & watertight-ish)
    mesh = poisson_mesh_from_pcd(
        pcd, depth=poisson_depth, smooth_iters=smooth_iters, crop_by_density=True
    )
    V = np.asarray(mesh.vertices).astype(np.float64)
    F = np.asarray(mesh.triangles).astype(np.int64)

    # 3) DDG: principal curvatures (k1,k2) & directions (d1,d2)
    k1, k2, d1, d2 = robust_principal_curvature(V, F)
    H = 0.5 * (k1 + k2)           # mean curvature
    K = k1 * k2                   # Gaussian curvature

    # 4) Laplace–Beltrami spectrum & HKS
    evals, evecs = laplace_beltrami_spectrum(V, F, k=n_eigs)
    # Drop the first eigenvector if it looks constant (λ≈0)
    if evals[0] < 1e-9:
        evecs_spec = evecs[:, 1: min(evecs.shape[1], 1 + 8)]  # 8 smooth modes by default
    else:
        evecs_spec = evecs[:, :min(evecs.shape[1], 8)]

    HKS = hks_from_spectrum(evals, evecs, ts=hks_times)  # (n, T)

    # 5) Feature stack (normalize each column)
    feat = np.c_[H, K, HKS, evecs_spec]  # local (H,K), multiscale (HKS), global (eigenmodes)
    feat = (feat - feat.mean(0)) / (feat.std(0) + 1e-12)

    # 6) Cluster
    labels = KMeans(n_clusters=k_clusters, n_init=10, random_state=0).fit_predict(feat)

    # 7) Colorize mesh by labels for visualization
    colors = np.random.RandomState(0).rand(k_clusters, 3)
    mesh.vertex_colors = o3d.utility.Vector3dVector(colors[labels])

    return mesh, labels


In [33]:
mesh, labels = segment_mesh_ddg(
    "./point_cloud_data/shoe/shoe-poisson-sampled.ply",
    voxel_size=0.003,
    normal_radius=0.01,
    poisson_depth=10,
    smooth_iters=10,
    n_eigs=50,
    k_clusters=6,
)
o3d.visualization.draw_geometries([mesh])

: 

In [2]:
# STL -> DDG segmentation (principal curvatures + spectra + HKS)
# --------------------------------------------------------------
# pip install open3d pyigl numpy scipy scikit-learn

import numpy as np
import open3d as o3d
import igl
from sklearn.cluster import KMeans
from scipy.sparse.linalg import eigsh
from scipy.sparse import issparse

# ---------- utilities ----------

def clean_mesh_o3d(mesh: o3d.geometry.TriangleMesh,
                   taubin_iters: int = 0,
                   keep_largest: bool = True) -> o3d.geometry.TriangleMesh:
    """Robust mesh cleanup for STL imports."""
    mesh.remove_unreferenced_vertices()
    mesh.remove_duplicated_vertices()
    mesh.remove_degenerate_triangles()
    mesh.remove_duplicated_triangles()
    mesh.remove_non_manifold_edges()

    # Optionally keep the largest connected component
    if keep_largest:
        labels = np.array(mesh.cluster_connected_triangles()[0])
        if labels.size > 0:
            # keep faces with the modal label
            counts = np.bincount(labels)
            keep = np.argmax(counts)
            face_mask = labels == keep
            idx = np.where(face_mask)[0].tolist()
            mesh = mesh.select_by_index(idx, retain_triangle_indices=True)

    mesh.remove_unreferenced_vertices()

    if taubin_iters and taubin_iters > 0:
        mesh = mesh.filter_smooth_taubin(number_of_iterations=taubin_iters)

    mesh.compute_vertex_normals()
    return mesh


def robust_principal_curvature(V, F):
    """
    Call igl.principal_curvature with robust unpacking across pyigl wheels.
    Returns:
        k1, k2 : (n,) float arrays   principal curvature values
        d1, d2 : (n,3) float arrays  principal directions
    """
    outs = igl.principal_curvature(V, F)
    if isinstance(outs, tuple):
        if len(outs) >= 4:
            PD1, PD2, PV1, PV2 = outs[:4]
        else:
            raise RuntimeError(f"Unexpected outputs from principal_curvature: {len(outs)}")
    else:
        PD1, PD2, PV1, PV2 = outs.PD1, outs.PD2, outs.PV1, outs.PV2

    PD1, PD2 = np.asarray(PD1), np.asarray(PD2)
    k1 = np.asarray(PV1).reshape(-1)
    k2 = np.asarray(PV2).reshape(-1)
    return k1, k2, PD1, PD2


def laplace_beltrami_spectrum(V, F, k=50):
    """
    Cotangent Laplacian L and Voronoi mass A; generalized eig: L u = λ A u.
    Returns k smallest eigenpairs.
    """
    L = igl.cotmatrix(V, F)                           # sparse
    A = igl.massmatrix(V, F, igl.MASSMATRIX_TYPE_VORONOI)
    assert issparse(L) and issparse(A)
    evals, evecs = eigsh(L.asfptype(), k=k, M=A.asfptype(), sigma=0.0)
    evals, evecs = np.real(evals), np.real(evecs)
    order = np.argsort(evals)
    return evals[order], evecs[:, order]


def hks_from_spectrum(evals, evecs, ts=(1e-4, 1e-3, 1e-2, 1e-1)):
    """Heat Kernel Signature at multiple times."""
    phi2 = evecs**2
    HKS = []
    for t in ts:
        HKS.append(phi2 @ np.exp(-evals*t))
    return np.stack(HKS, axis=1)   # (n, |ts|)


# ---------- main pipeline ----------

def segment_stl_ddg(
    stl_path: str,
    taubin_iters: int = 5,
    n_eigs: int = 50,
    use_hks: bool = True,
    hks_times=(1e-4, 1e-3, 1e-2, 1e-1),
    n_spectral_coords: int = 8,   # low-freq eigenvectors used as global coords
    k_clusters: int = 6,
    random_state: int = 0,
):
    """
    STL -> clean -> DDG features (k1,k2,H,K,+spectra [+HKS]) -> KMeans.
    Returns:
        mesh_o3d (with vertex colors), labels (per-vertex)
    """
    # 1) Load STL
    mesh = o3d.io.read_triangle_mesh(stl_path)
    if mesh.is_empty():
        raise ValueError(f"Could not read a valid mesh from: {stl_path}")

    # 2) Clean & (optionally) smooth
    mesh = clean_mesh_o3d(mesh, taubin_iters=taubin_iters, keep_largest=True)

    # Export numpy arrays for libigl
    V = np.asarray(mesh.vertices).astype(np.float64)
    F = np.asarray(mesh.triangles).astype(np.int64)
    if V.shape[0] == 0 or F.shape[0] == 0:
        raise ValueError("Mesh has no vertices or faces after cleaning.")

    # 3) DDG: principal curvatures
    k1, k2, d1, d2 = robust_principal_curvature(V, F)
    H = 0.5*(k1 + k2)            # mean curvature
    K = k1 * k2                  # Gaussian curvature

    # 4) Spectrum (Laplace–Beltrami)
    evals, evecs = laplace_beltrami_spectrum(V, F, k=n_eigs)

    # pick a few smooth eigenvectors as global coords (skip constant)
    start = 1 if evals[0] < 1e-12 else 0
    stop  = min(evecs.shape[1], start + n_spectral_coords)
    spectral = evecs[:, start:stop] if stop > start else np.zeros((V.shape[0], 0))

    # 5) Optional multi-scale HKS
    if use_hks:
        HKS = hks_from_spectrum(evals, evecs, ts=hks_times)
    else:
        HKS = np.zeros((V.shape[0], 0))

    # 6) Feature stack (and z-score)
    feat = np.c_[H, K, HKS, spectral]
    feat = (feat - feat.mean(axis=0)) / (feat.std(axis=0) + 1e-12)

    # 7) Cluster
    labels = KMeans(n_clusters=k_clusters, n_init=10, random_state=random_state)\
             .fit_predict(feat)

    # 8) Colorize for visualization
    colors = np.random.RandomState(random_state).rand(k_clusters, 3)
    mesh.vertex_colors = o3d.utility.Vector3dVector(colors[labels])

    return mesh, labels


Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [4]:
# ---------- example usage ----------
mesh, labels = segment_stl_ddg(
    "./stl_data/shoe/shoe1.stl",
    taubin_iters=10,       # more smoothing = more stable curvature
    n_eigs=60,
    use_hks=True,
    k_clusters=5,
)
o3d.visualization.draw_geometries([mesh])
o3d.io.write_triangle_mesh("segmented_from_stl.ply", mesh)

TypeError: select_by_index(): incompatible function arguments. The following argument types are supported:
    1. (self: open3d.cpu.pybind.geometry.TriangleMesh, indices: list[int], cleanup: bool = True) -> open3d.cpu.pybind.geometry.TriangleMesh

Invoked with: TriangleMesh with 246869 points and 494426 triangles., [1281, 1282, 1283, 1284, 1285, 1286, 1287, 1288, 1289, 1290, 1291, 1292, 1293, 1294, 1295, 1296, 1297, 1298, 1299, 1300, 1301, 1302, 1303, 1304, 1305, 1306, 1307, 1308, 1309, 1310, 1311, 1312, 1313, 1314, 1315, 1316, 1317, 1318, 1319, 1320, 1321, 1322, 1323, 1324, 1325, 1326, 1327, 1328, 1329, 1330, 1331, 1332, 1333, 1334, 1335, 1336, 1337, 1338, 1339, 1340, 1341, 1342, 1343, 1551, 1552, 1553, 1554, 1555, 1556, 1557, 1558, 1559, 1560, 1561, 1562, 1563, 1564, 1565, 1566, 1567, 1568, 1569, 1570, 1571, 1572, 1573, 1574, 1575, 1576, 1577, 1578, 1579, 1580, 1581, 1582, 1583, 1584, 1585, 1586, 1587, 1588, 1589, 1590, 1591, 1592, 1593, 1594, 1595, 1596, 1597, 1598, 1599, 1600, 1601